In [1]:
!pip install selenium

In [2]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import csv
import os
import time

from selenium.webdriver.common.action_chains import ActionChains

In [3]:
service = Service(executable_path="./chromedriver")
driver = webdriver.Chrome(service=service)
csv_file_path = "job_data_Nextera.csv"

file_exists = os.path.isfile(csv_file_path)
file_empty = os.stat(csv_file_path).st_size == 0 if file_exists else True


# Write the header row if the file doesn't exist or is empty
if not file_exists or file_empty:
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["Job Title", "Job Description"])
driver.get("https://jobs.nexteraenergy.com/search/?searchby=location&createNewAlert=false&q=Wind&locationsearch=&geolocation=&optionsFacetsDD_customfield1=&optionsFacetsDD_customfield2=&optionsFacetsDD_customfield3=")


# Function to get elements with retry
def get_elements_with_retry(driver, by, value, max_attempts=3):
    attempts = 0
    while attempts < max_attempts:
        try:
            elements = WebDriverWait(driver, 10).until(
                EC.presence_of_all_elements_located((by, value))
            )
            return elements
        except StaleElementReferenceException:
            attempts += 1
    return []

# Function to get element text with retry
def get_element_text_with_retry(element, max_attempts=3):
    attempts = 0
    while attempts < max_attempts:
        try:
            return element.text
        except StaleElementReferenceException:
            attempts += 1
    return ""

job_id = "jobTitle-link"
jobs = get_elements_with_retry(driver, By.CLASS_NAME, job_id)

#job
for j in jobs:
    try:
        job_title = get_element_text_with_retry(j)
        j.click()
        
        # Wait for job description to load
        job_description_element = WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CLASS_NAME, "job"))
        )
        job_description = get_element_text_with_retry(job_description_element)
        
        with open(csv_file_path, mode='a', newline='', encoding='utf-8') as file:
            writer = csv.writer(file)
            writer.writerow([job_title, job_description])
        
        # Navigate back to the job list
        driver.back()
        
        # Wait for the job list to reload
        WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CLASS_NAME, job_id))
        )
        
        # Re-fetch the job elements
        jobs = get_elements_with_retry(driver, By.CLASS_NAME, job_id)
    except Exception as e:
        print(f"Error processing job: {e}")
        continue

driver.quit()


WebDriverException: Message: Service ./chromedriver unexpectedly exited. Status code was: -9


In [32]:

service = Service(executable_path="./chromedriver")
driver = webdriver.Chrome(service=service)
csv_file_path = "job_data_Nextera.csv"

# Check if the file exists and is empty
file_exists = os.path.isfile(csv_file_path)
file_empty = os.stat(csv_file_path).st_size == 0 if file_exists else True

# Write the header row if the file doesn't exist or is empty
if not file_exists or file_empty:
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["Job Title", "Job Description"])

driver.get("https://jobs.nexteraenergy.com/search/?q=Wind&searchby=location&d=10&startrow=0")

# Function to get elements with retry
def get_elements_with_retry(driver, by, value, max_attempts=3):
    attempts = 0
    while attempts < max_attempts:
        try:
            elements = WebDriverWait(driver, 10).until(
                EC.presence_of_all_elements_located((by, value))
            )
            return elements
        except StaleElementReferenceException:
            attempts += 1
    return []

# Function to get element text with retry
def get_element_text_with_retry(element, max_attempts=3):
    attempts = 0
    while attempts < max_attempts:
        try:
            return element.text
        except StaleElementReferenceException:
            attempts += 1
    return ""

job_id = "jobTitle-link"

while True:
    jobs = get_elements_with_retry(driver, By.CLASS_NAME, job_id)
    
    if not jobs:
        break  # Exit the loop if no more jobs are found
    
    for j in jobs:
        try:
            # Scroll the job into view
            ActionChains(driver).move_to_element(j).perform()
            
            job_title = get_element_text_with_retry(j)
            j.click()
            
            # Wait for job description to load
            job_description_element = WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CLASS_NAME, "job"))
            )
            job_description = get_element_text_with_retry(job_description_element)
            
            with open(csv_file_path, mode='a', newline='', encoding='utf-8') as file:
                writer = csv.writer(file)
                writer.writerow([job_title, job_description])
            
            # Navigate back to the job list
            driver.back()
            
            # Wait for the job list to reload
            WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CLASS_NAME, job_id))
            )
            
        except Exception as e:
            print(f"Error processing job: {e}")
            continue
    
    # Scroll to the bottom of the page to load more jobs
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    time.sleep(2)  # Wait for new content to load

driver.quit()

Error processing job: Message: stale element reference: stale element not found
  (Session info: chrome=126.0.6478.183); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#stale-element-reference-exception
Stacktrace:
0   chromedriver                        0x000000010245aa80 chromedriver + 4385408
1   chromedriver                        0x000000010245338c chromedriver + 4354956
2   chromedriver                        0x0000000102070b0c chromedriver + 281356
3   chromedriver                        0x000000010207e898 chromedriver + 338072
4   chromedriver                        0x0000000102075d84 chromedriver + 302468
5   chromedriver                        0x0000000102074678 chromedriver + 296568
6   chromedriver                        0x0000000102076e58 chromedriver + 306776
7   chromedriver                        0x0000000102076ed0 chromedriver + 306896
8   chromedriver                        0x00000001020b8448 chrom

KeyboardInterrupt: 

In [33]:
import pandas as pd

# Load the CSV file
file_path = 'job_data_Nextera.csv'
df = pd.read_csv(file_path)

# Drop duplicates based on the first column
df_no_duplicates = df.drop_duplicates(subset=df.columns[0])

# Save the resulting DataFrame to a new CSV file
output_file_path = 'job_data_Nextera_no_duplicates.csv'
df_no_duplicates.to_csv(output_file_path, index=False)

print(f"Reformatted CSV file saved to {output_file_path}")


Reformatted CSV file saved to job_data_Nextera_no_duplicates.csv


In [35]:
import os
import csv
import time
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException, NoSuchElementException
from selenium.webdriver.common.action_chains import ActionChains

# Initialize the Chrome WebDriver
service = Service(executable_path="./chromedriver")
driver = webdriver.Chrome(service=service)

csv_file_path = "job_data_Nextera.csv"

# Check if the file exists and is empty
file_exists = os.path.isfile(csv_file_path)
file_empty = os.stat(csv_file_path).st_size == 0 if file_exists else True

# Write the header row if the file doesn't exist or is empty
if not file_exists or file_empty:
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["Job Title", "Job Description"])

# Function to get elements with retry
def get_elements_with_retry(driver, by, value, max_attempts=3):
    attempts = 0
    while attempts < max_attempts:
        try:
            elements = WebDriverWait(driver, 10).until(
                EC.presence_of_all_elements_located((by, value))
            )
            return elements
        except (StaleElementReferenceException, NoSuchElementException):
            attempts += 1
    return []

# Function to get element text with retry
def get_element_text_with_retry(element, max_attempts=3):
    attempts = 0
    while attempts < max_attempts:
        try:
            return element.text
        except StaleElementReferenceException:
            attempts += 1
    return ""

# Base URL for the job listings
base_url = "https://jobs.nexteraenergy.com/search/?q=Wind&searchby=location&d=10&startrow="

# Initialize startrow parameter for pagination
startrow = 0

while True:
    # Construct the URL for the current page
    current_url = f"{base_url}{startrow}"
    driver.get(current_url)
    
    # Wait for the job list to load
    time.sleep(5)
    
    jobs = get_elements_with_retry(driver, By.CLASS_NAME, "jobTitle-link")
    
    if not jobs:
        break  # Exit the loop if no more jobs are found
    
    for j in range(len(jobs)):
        try:
            # Refresh job links list and scroll the job into view
            jobs = get_elements_with_retry(driver, By.CLASS_NAME, "jobTitle-link")
            job = jobs[j]
            
            job_title = get_element_text_with_retry(job)
            ActionChains(driver).move_to_element(job).perform()
            job.click()
            
            # Wait for job description to load
            job_description_element = WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CLASS_NAME, "job"))
            )
            job_description = get_element_text_with_retry(job_description_element)
            
            with open(csv_file_path, mode='a', newline='', encoding='utf-8') as file:
                writer = csv.writer(file)
                writer.writerow([job_title, job_description])
            
            # Navigate back to the job list
            driver.back()
            
            # Wait for the job list to reload
            WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CLASS_NAME, "jobTitle-link"))
            )
            
        except Exception as e:
            print(f"Error processing job: {e}")
            continue
    
    # Increment the startrow parameter for the next page
    startrow += 25

driver.quit()

print(f"Job data has been appended to {csv_file_path}")


Error processing job: Message: javascript error: {"status":60,"value":"https://jobs.nexteraenergy.com/job/Sterling-City-Wind-Field-Service-Technician-III-Capricorn-Ridge-Sterling-City%2C-TX-TX-76951/1192498400/ has no size and location"}
  (Session info: chrome=126.0.6478.183)
Stacktrace:
0   chromedriver                        0x0000000104c52a80 chromedriver + 4385408
1   chromedriver                        0x0000000104c4b38c chromedriver + 4354956
2   chromedriver                        0x0000000104868b0c chromedriver + 281356
3   chromedriver                        0x000000010486cfd8 chromedriver + 298968
4   chromedriver                        0x000000010486ee58 chromedriver + 306776
5   chromedriver                        0x000000010486eed0 chromedriver + 306896
6   chromedriver                        0x00000001048b0448 chromedriver + 574536
7   chromedriver                        0x00000001048afb58 chromedriver + 572248
8   chromedriver                        0x00000001048eaea8 c

KeyboardInterrupt: 

In [37]:
import pandas as pd

# Load the CSV file
file_path = 'job_data_Nextera.csv'
df = pd.read_csv(file_path)

# Drop duplicates based on the first column
df_no_duplicates = df.drop_duplicates(subset=df.columns[0])

# Save the resulting DataFrame to a new CSV file
output_file_path = 'job_data_Nextera_no_duplicates.csv'
df_no_duplicates.to_csv(output_file_path, index=False)

print(f"Reformatted CSV file saved to {output_file_path}")

Reformatted CSV file saved to job_data_Nextera_no_duplicates.csv
